In [1]:
import numpy as np
import pandas as pd
import copy
import random
import time
import pickle
import sys
import logging
logging.basicConfig(stream=sys.stdout, level=logging.INFO)

from util.util_load             import read_txt, read_scenario
from util.util_reschedule       import random_events, store_schedule, update_schedule, snapshot
from util.util_display          import plot, pretty_table
from env_action.metaheu         import GeneticAlgorithm, random_population
from env_action.action_space    import action_space

maxtime                = 2
PopSize                = 100
critical_machines      = {5, 6, 7, 8, 9, 10, 11, 12, 13, 21, 22, 26, 27}
action_name            = ["GA", "TS", 
                          "LFOH", "LAPH", "LAP_LFO", 
                          "LFOH_TS", "LAPH_TS", "LFOH_GA", "LAPH_GA",
                          "CDR1", "CDR2", "CDR3", "CDR4", "CDR5", "CDR6",
                          "RCRS"]
K = 30

with open('pickle_instances_480.pkl', 'rb') as f:
    instances = pickle.load(f)

instance_id = '_fixed_instance'
current_instance 	= instances[instance_id]
J 					= current_instance.J
I 					= current_instance.I
X_ijk 				= current_instance.X_ijk
S_ij 				= current_instance.S_ij
C_ij 				= current_instance.C_ij
C_j 				= current_instance.C_j
p_ijk 				= current_instance.p_ijk
h_ijk 				= current_instance.h_ijk
d_j 				= current_instance.d_j
n_j 				= current_instance.n_j
MC_ji				= current_instance.MC_ji
n_MC_ji 			= current_instance.n_MC_ji
OperationPool 		= current_instance.OperationPool
n_Mch               = np.sum(np.max(h_ijk, axis= (0, 1)))/K
org_J               = copy.deepcopy(J)
org_p_ijk      	    = copy.deepcopy(p_ijk)
org_h_ijk      	    = copy.deepcopy(h_ijk)
org_n_j        	    = copy.deepcopy(n_j)
org_MC_ji      	    = copy.deepcopy(MC_ji)
org_n_MC_ji    	    = copy.deepcopy(n_MC_ji)


# J, I, K, p_ijk, h_ijk,   \
# d_j, n_j, MC_ji, n_MC_ji,\
# OperationPool            = read_txt("DATA/jobs_small.txt")
JA_event, MB_event       = read_scenario("DATA/SMALL/Scenario_fixed_scenario_480.txt", K, critical_machines)

# variables = ['J', 'p_ijk', 'h_ijk', 'n_j', 'MC_ji', 'n_MC_ji']
# for var in variables:
#     globals()['org_' + var] = copy.deepcopy(globals()[var])

S_k                    = np.zeros((K))
S_j                    = np.zeros((J))
n_ops_left_j           = copy.deepcopy(n_j)

t                      = 0
JSet                   = list(range(J))
OJSet                  = [[] for _ in range(J)]
for j in JSet:
    OJSet[j]           = [i for i in range(int(n_j[j]))]

events                 = {}
MB_record              = {}

# Preschedule
print("preschedule")


# StartTime                     = time.time()
# population, chromosome_len    = random_population(OperationPool, PopSize)
# GBest, X_ijk, S_ij, C_ij, C_j = GeneticAlgorithm(S_k, S_j, JSet, OJSet, J, I, K, 
#                                                 p_ijk, h_ijk, d_j, n_j, n_ops_left_j, 
#                                                 MC_ji, n_MC_ji, OperationPool,
#                                                 PopSize, population, chromosome_len,
#                                                 StartTime, maxtime=1000)
# print("time elapsed", time.time() - StartTime)

fig1 = plot(J, K, n_j, X_ijk, S_ij, C_ij, MB_record, t)
display(fig1)

preschedule


In [2]:
# Running schedule
completion = False
# Random events
print("random event")
JA_event, MB_event, t, triggered_event, \
affected_Oij, re, MB_record                           = random_events(t, J, K, X_ijk, S_ij, C_ij, C_j, JA_event, MB_event, MB_record)


while completion == False and triggered_event is not None:
    if t < np.max(C_ij):
        print('----------------------------------------')
        print(t, triggered_event)
        print("snapshot")
        # Snapshot
        S_k, S_j, J, I, JSet, OJSet, DSet, ODSet, OperationPool, \
        n_ops_left_j, MC_ji, n_MC_ji, d_j, n_j, p_ijk, h_ijk,    \
        org_p_ijk, org_h_ijk, org_n_j, org_MC_ji, org_n_MC_ji,   \
        Oij_on_machine, X_ijk, S_ij, C_ij, C_j,                  \
        JA_boolean, JA_long_boolean, JA_urgent_boolean,          \
        MB_boolean, MB_critical_boolean, sum_re,                 \
        CT_k, T_cur, Tard_job, NewJobList            = snapshot(t, triggered_event, MC_ji, n_MC_ji,                 \
                                                                d_j, n_j, p_ijk, h_ijk, J, I, K, X_ijk, S_ij, C_ij, \
                                                                OperationPool, re, S_k,                             \
                                                                org_J, org_p_ijk, org_h_ijk, org_n_j,               \
                                                                org_MC_ji, org_n_MC_ji, C_j                         )
        # Store previous schedule
        print("store schedule")
        X_previous, S_previous, C_previous           = store_schedule(X_ijk, S_ij, C_ij)       
        action_method 						         = action_space(J, I, K, p_ijk, h_ijk, d_j, n_j, 
                                                                    MC_ji, n_MC_ji, n_ops_left_j, OperationPool, S_k, S_j, 
                                                                    JSet, OJSet, Oij_on_machine, affected_Oij, 
                                                                    t, X_ijk, S_ij, C_ij, C_j, CT_k, T_cur, Tard_job,
                                                                    NewJobList, PopSize, maxtime)
        action_id                                    = 1
        print(action_name[action_id])

        reschedule							         = action_method[action_id]
        GBest, X_ijk, S_ij, C_ij, C_j                = reschedule()
        print(GBest)
        print("update_schedule")
        X_ijk, S_ij, C_ij, C_j                        = update_schedule(DSet, ODSet, X_ijk, S_ij, C_ij, X_previous, S_previous, C_previous)
        fig2 = plot(J, K, n_j, X_ijk, S_ij, C_ij, MB_record, t)
        display(fig2)
        
        print("random_events")
        JA_event, MB_event, t, triggered_event,\
        affected_Oij, re, MB_record                   = random_events(t, J, K, X_ijk, S_ij, C_ij, C_j, JA_event, MB_event, MB_record)
    else: completion = True


random event
JA_event [(41, 1, 'urgent'), (99, 3, 'urgent'), (128, 9, 'urgent'), (160, 1, 'urgent'), (175, 4, 'urgent'), (188, 1, 'urgent'), (225, 2, 'urgent'), (288, 2, 'urgent'), (441, 9, 'urgent'), (562, 5, 'urgent'), (634, 9, 'urgent')]
MB_event [[], [], [], [], [], [], [], [], [], [], [(21480.0, 2220.0, 'critical')], [], [(15300.0, 3540.0, 'critical')], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []]
----------------------------------------
7550 [('MB', 10, 840.0, 'critical')]
snapshot
store schedule
TS
check OA [39, 8, 28, 48, 282, 264, 39, 172, 200, 536, 272, 230, 559, 80, 131, 105, 10, 184, 8, 232, 228, 101, 8, 360, 89, 259, 318, 192, 631, 24, 334, 544, 101, 222, 207, 42, 15, 381, 173, 11, 312, 121, 261, 561, 200, 279, 234, 549, 544, 11, 241, 35, 141, 590, 68, 67, 15, 10, 534, 40, 264, 134, 76, 601, 528, 616, 580, 223, 161, 40, 344, 639, 13, 127, 117, 299, 10, 276, 13, 496, 127, 414, 159, 167, 325, 258, 11, 10, 543, 33, 574, 580, 82, 11, 102, 19, 294, 14, 56

random_events
JA_event [(41, 1, 'urgent'), (99, 3, 'urgent'), (128, 9, 'urgent'), (160, 1, 'urgent'), (175, 4, 'urgent'), (188, 1, 'urgent'), (225, 2, 'urgent'), (288, 2, 'urgent'), (441, 9, 'urgent'), (562, 5, 'urgent'), (634, 9, 'urgent')]
MB_event [[], [], [], [], [], [], [], [], [], [], [(21480.0, 2220.0, 'critical')], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []]
----------------------------------------
15300 [('MB', 12, 3540.0, 'critical')]
snapshot
store schedule
TS
check OA [154, 546, 630, 83, 98, 525, 137, 253, 36, 549, 36, 144, 288, 83, 52, 97, 448, 574, 41, 628, 237, 155, 519, 533, 503, 263, 71, 288, 541, 629, 138, 543, 588, 71, 346, 194, 50, 170, 431, 562, 169, 125, 275, 187, 556, 533, 162, 566, 615, 208, 124, 561, 126, 100, 248, 294, 592, 128, 100, 53, 136, 217, 558, 556, 121, 225, 408, 119, 57, 43, 94, 54, 296, 43, 85, 454, 230, 58, 132, 94, 46, 111, 567, 558, 81, 78, 46, 200, 211, 104, 47, 111, 56, 44, 144, 159, 44, 578, 220, 256, 104, 235, 

random_events
JA_event [(99, 3, 'urgent'), (128, 9, 'urgent'), (160, 1, 'urgent'), (175, 4, 'urgent'), (188, 1, 'urgent'), (225, 2, 'urgent'), (288, 2, 'urgent'), (441, 9, 'urgent'), (562, 5, 'urgent'), (634, 9, 'urgent')]
MB_event [[], [], [], [], [], [], [], [], [], [], [(21480.0, 2220.0, 'critical')], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []]
----------------------------------------
15510 [('JA', 41, 1, 'urgent')]
snapshot
store schedule
TS
check OA [640, 640, 640, 640, 640, 263, 71, 346, 288, 431, 448, 541, 629, 237, 275, 543, 588, 194, 50, 562, 169, 170, 100, 138, 187, 533, 556, 162, 566, 615, 294, 208, 124, 561, 136, 125, 100, 248, 592, 126, 408, 53, 128, 94, 556, 558, 225, 121, 85, 217, 57, 43, 230, 111, 54, 43, 296, 119, 58, 46, 104, 111, 94, 558, 567, 78, 81, 200, 46, 454, 220, 47, 104, 235, 132, 56, 44, 112, 144, 159, 44, 578, 211, 108, 208, 564, 567, 215, 147, 631, 237, 256, 250, 122, 161, 108, 126, 48, 60, 180, 166, 228, 116, 232, 257, 52, 

random_events
JA_event [(128, 9, 'urgent'), (160, 1, 'urgent'), (175, 4, 'urgent'), (188, 1, 'urgent'), (225, 2, 'urgent'), (288, 2, 'urgent'), (441, 9, 'urgent'), (562, 5, 'urgent'), (634, 9, 'urgent')]
MB_event [[], [], [], [], [], [], [], [], [], [], [(21480.0, 2220.0, 'critical')], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []]
----------------------------------------
19485 [('JA', 99, 3, 'urgent')]
snapshot
store schedule
TS
check OA [641, 641, 641, 641, 641, 152, 507, 319, 96, 345, 89, 252, 353, 134, 251, 132, 348, 375, 178, 299, 349, 281, 582, 88, 85, 373, 135, 359, 91, 92, 85, 382, 366, 364, 90, 281, 229, 92, 280, 367, 372, 295, 86, 389, 159, 93, 267, 391, 138, 259, 134, 261, 286, 609, 93, 110, 145, 107, 446, 634, 418, 113, 110, 95, 310, 612, 393, 422, 399, 94, 286, 250, 424, 303, 350, 419, 295, 103, 94, 351, 423, 158, 352, 311, 551, 102, 483, 100, 315, 357, 98, 428, 492, 100, 593, 322, 362, 636, 434, 387, 104, 326, 265, 225, 394, 457, 109, 401, 333

random_events
JA_event [(128, 9, 'urgent'), (160, 1, 'urgent'), (175, 4, 'urgent'), (188, 1, 'urgent'), (225, 2, 'urgent'), (288, 2, 'urgent'), (441, 9, 'urgent'), (562, 5, 'urgent')]
MB_event [[], [], [], [], [], [], [], [], [], [], [(21480.0, 2220.0, 'critical')], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []]
----------------------------------------
20290 [('JA', 634, 9, 'urgent')]
snapshot
store schedule
TS
check OA [642, 642, 642, 642, 642, 642, 104, 110, 460, 403, 195, 94, 103, 109, 467, 404, 593, 405, 343, 243, 102, 100, 115, 415, 474, 417, 98, 285, 488, 194, 269, 468, 356, 100, 425, 497, 111, 441, 369, 225, 106, 636, 482, 444, 108, 371, 478, 106, 213, 506, 392, 114, 370, 384, 113, 489, 97, 112, 123, 283, 103, 191, 177, 187, 157, 105, 158, 128, 296, 583, 131, 112, 118, 172, 623, 175, 207, 170, 179, 191, 156, 129, 117, 293, 116, 256, 129, 116, 169, 594, 619, 624, 119, 120, 119, 140, 125, 181, 120, 122, 134, 124, 173, 131, 146, 151, 122, 130, 628, 269,

random_events
JA_event [(128, 9, 'urgent'), (160, 1, 'urgent'), (175, 4, 'urgent'), (188, 1, 'urgent'), (225, 2, 'urgent'), (288, 2, 'urgent'), (562, 5, 'urgent')]
MB_event [[], [], [], [], [], [], [], [], [], [], [(21480.0, 2220.0, 'critical')], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []]
----------------------------------------
20535 [('JA', 441, 9, 'urgent')]
snapshot
store schedule
TS
check OA [643, 643, 444, 392, 506, 489, 478, 114, 642, 370, 123, 384, 642, 283, 177, 158, 103, 642, 583, 100, 110, 100, 269, 636, 175, 106, 170, 106, 213, 97, 113, 156, 112, 103, 116, 191, 187, 116, 169, 105, 157, 624, 296, 119, 128, 112, 119, 120, 131, 125, 118, 151, 172, 131, 120, 623, 628, 126, 124, 207, 273, 191, 179, 127, 117, 183, 129, 128, 293, 581, 256, 126, 129, 569, 594, 619, 136, 140, 193, 181, 134, 196, 146, 122, 269, 211, 173, 122, 156, 540, 217, 130, 133, 192, 591, 505, 249, 190, 180, 130, 137, 153, 136, 138, 137, 155, 176, 132, 199, 147, 135, 133, 150, 13

random_events
JA_event [(128, 9, 'urgent'), (160, 1, 'urgent'), (175, 4, 'urgent'), (188, 1, 'urgent'), (225, 2, 'urgent'), (288, 2, 'urgent'), (562, 5, 'urgent')]
MB_event [[], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []]


In [3]:
for k in range(K):
    print(k+1, S_k[k])

1 20535.0
2 20535.0
3 20535.0
4 20535.0
5 20535.0
6 20535.0
7 20535.0
8 20535.0
9 20535.0
10 20630.0
11 20535.0
12 20535.0
13 20540.0
14 20535.0
15 20535.0
16 20535.0
17 20535.0
18 20535.0
19 20535.0
20 20535.0
21 20575.0
22 20535.0
23 20535.0
24 20535.0
25 20535.0
26 20535.0
27 20540.0
28 20535.0
29 20535.0
30 20560.0


In [4]:
# table = pretty_table(J, I, n_j, X_ijk, S_ij, C_ij)
# table = table[table['Job'] == 13]
# display(table)